In [2]:
%load_ext autoreload
%autoreload 2

# Import necessary modules 
import numpy as np
import pandas as pd
from itertools import product
import plotly.graph_objs as go
import plotly.express as px
from numpy.linalg import eigvalsh
from plotly.subplots import make_subplots

from rbf_volatility_surface import RBFVolatilitySurface
from smoothness_prior import RBFQuadraticSmoothnessPrior
from dataset_sabr import generate_sabr_call_options

In [2]:
# Define the strike price list and maturity time list
strike_price_list = np.array([0.75, 0.85, 0.9, 0.95, 1.0, 1.05, 1.1, 1.2, 1.3, 1.5])
maturity_time_list = np.array([0.02, 0.08, 0.17, 0.25, 0.5, 0.75, 1.0, 1.5, 2.0, 3.0])

# Create the product grid of maturity times and strike prices
product_grid = list(product(maturity_time_list, strike_price_list))
maturity_times, strike_prices = zip(*product_grid)

# Convert to arrays for further operations
maturity_times = np.array(maturity_times)
strike_prices = np.array(strike_prices)

# Variance formula for log-uniform distribution
def log_uniform_variance(a, b):
    log_term = np.log(b / a)
    var = ((b ** 2 - a ** 2) / (2 * log_term)) - ((b - a) / log_term) ** 2
    return var

# Calculate standard deviations for maturity times and strike prices
maturity_std = np.sqrt(log_uniform_variance(maturity_time_list.min(), maturity_time_list.max()))
strike_std = np.sqrt(log_uniform_variance(strike_price_list.min(), strike_price_list.max()))

# Define the SABR model parameters
alpha = 0.20  # Stochastic volatility parameter
beta = 0.50   # Elasticity parameter
rho = -0.75   # Correlation between asset price and volatility
nu = 1.0      # Volatility of volatility parameter

# Other model parameters
risk_free_rate = np.log(1.02)  # Risk-free interest rate
underlying_price = 1.0         # Current price of the underlying asset

# Generate the dataset using the SABR model and Black-Scholes formula
call_option_dataset = generate_sabr_call_options(
    alpha=alpha,
    beta=beta,
    rho=rho,
    nu=nu,
    maturity_times=maturity_times,
    strike_prices=strike_prices,
    risk_free_rate=risk_free_rate,
    underlying_price=underlying_price
)

# Maturity times and strike prices from the previous product grid setup
hypothetical_maturity_time_list = np.logspace(np.log10(0.01), np.log10(3.1), 100)
hypothetical_strike_price_list = np.logspace(np.log10(0.7), np.log10(1.75), 100)

# Create the product grid of maturity times and strike prices
hypothetical_product_grid = list(product(hypothetical_maturity_time_list, hypothetical_strike_price_list))
hypothetical_maturity_times, hypothetical_strike_prices = zip(*hypothetical_product_grid)
hypothetical_maturity_times, hypothetical_strike_prices = np.array(hypothetical_maturity_times), np.array(hypothetical_strike_prices)

# Reshape the data for 3D surface plotting
hypothetical_maturities_grid = hypothetical_maturity_times.reshape((len(hypothetical_maturity_time_list), len(hypothetical_strike_price_list)))  
hypothetical_strikes_grid = hypothetical_strike_prices.reshape((len(hypothetical_maturity_time_list), len(hypothetical_strike_price_list)))

In [3]:
n_roots = 350
smoothness_controller = 3.274549162877732e-05

# Initialize the RBFQuadraticSmoothnessPrior class
smoothness_prior = RBFQuadraticSmoothnessPrior(
    maturity_times=maturity_times,
    strike_prices=strike_prices,
    maturity_std=maturity_std,
    strike_std=strike_std,
    n_roots=n_roots,
    smoothness_controller=smoothness_controller,
    random_state=0,
)

In [84]:
f_norm_regularizer = 1000000000

# Calculate the Frobenius norm of the observed implied volatility surface
data_frobenius_norm = np.linalg.norm(call_option_dataset["Implied Volatility"].values)

# Generate 100 log-spaced values for the smoothness controller (gamma)
smoothness_values = np.logspace(-6, -1, 100)

# Initialize a list to store log-likelihood values
regularized_log_likelihoods = []

# Loop through each smoothness value and calculate the log-likelihood
for gamma in smoothness_values:
    # Set the smoothness controller for the smoothness prior
    smoothness_prior.smoothness_controller = gamma
    
    # Calculate the log-likelihood for the current smoothness controller
    log_likelihood_value = smoothness_prior.log_likelihood(
        data_implied_volatilities=call_option_dataset["Implied Volatility"].values,
        data_maturity_times=call_option_dataset["Time to Maturity"].values,
        data_strike_prices=call_option_dataset["Strike Price"].values,
        risk_free_rate=risk_free_rate,
        underlying_price=underlying_price,
        noise_level=0
    )

    sqrt_expected_squared_frobenius_norm = smoothness_prior.square_root_expected_squared_frobenius_norm(
        data_implied_volatilities=call_option_dataset["Implied Volatility"].values,
        data_maturity_times=call_option_dataset["Time to Maturity"].values,
        data_strike_prices=call_option_dataset["Strike Price"].values,
        risk_free_rate=risk_free_rate,
        underlying_price=underlying_price,
    )

    regularized_log_likelihood = log_likelihood_value - \
        f_norm_regularizer * (data_frobenius_norm - sqrt_expected_squared_frobenius_norm) ** 2   
    
    # Append the log-likelihood value to the list
    regularized_log_likelihoods.append(regularized_log_likelihood)

# Convert the list of log-likelihoods to a NumPy array for easy processing
regularized_log_likelihoods = np.array(regularized_log_likelihoods)

# Find the optimal smoothness controller (the one with the maximum log-likelihood)
optimal_smoothness = smoothness_values[np.argmax(regularized_log_likelihoods)]
smoothness_prior.smoothness_controller = optimal_smoothness

# Create a Plotly figure to visualize the log-likelihoods
fig = go.Figure()

# Add a line plot for the log-likelihood values
fig.add_trace(
    go.Scatter(
        x=smoothness_values,
        y=-regularized_log_likelihoods,
        mode='lines+markers',
        name='Log-Likelihood',
        line=dict(color='royalblue', width=2),
        marker=dict(size=6)
    )
)

# Highlight the optimal smoothness controller with a vertical line
fig.add_trace(
    go.Scatter(
        x=[optimal_smoothness],
        y=[min(-regularized_log_likelihoods)],
        mode='markers',
        name=f'Optimal γ: {optimal_smoothness:.7f}',
        marker=dict(color='red', size=10, symbol='circle')
    )
)

# Update the layout for the plot
fig.update_layout(
    title="Minus Regularized Log-Likelihood vs Smoothness Controller",
    xaxis_title="Smoothness Controller (γ)",
    yaxis_title="Log-Likelihood",
    xaxis_type="log",  # Log scale for smoothness controller
    yaxis_type="log",
    height=900,
    width=900,
    legend=dict(x=0.1, y=0.9),
    title_x=0.5,
)

# Show the plot
fig.show()

# Print the optimal smoothness controller
print(f"Optimal smoothness controller: {optimal_smoothness}")

Optimal smoothness controller: 3.274549162877732e-05


In [70]:
# Calculate the prior covariance matrix
prior_covariance_matrix = smoothness_prior.prior_covariance()

# Display the covariance matrix
print("Prior Covariance Matrix:")
pd.DataFrame(prior_covariance_matrix)

Prior Covariance Matrix:


0             1             2             3             4   \
0   2.062325e-05 -8.292895e-05  6.763603e-05 -1.132442e-05 -5.281116e-06   
1  -8.292895e-05  6.090076e-04 -4.991509e-04  5.720341e-05  5.647063e-06   
2   6.763603e-05 -4.991509e-04  4.676175e-04 -6.820018e-05 -3.379895e-05   
3  -1.132442e-05  5.720341e-05 -6.820018e-05  1.954225e-04  4.322397e-06   
4  -5.281116e-06  5.647063e-06 -3.379895e-05  4.322397e-06  5.267382e-04   
..           ...           ...           ...           ...           ...   
95 -4.322173e-12  4.163222e-12  2.228691e-11  1.099926e-12 -2.824555e-11   
96 -1.493612e-12  7.803618e-12  4.862466e-13 -4.056137e-11 -5.496907e-12   
97 -1.229522e-13 -1.491222e-12  8.100457e-13  8.437023e-14  2.285556e-11   
98 -9.262361e-15  4.188281e-15 -1.541227e-15  1.055888e-14 -1.687721e-13   
99 -2.373004e-17  1.413190e-16  7.479754e-17 -7.653431e-16 -1.963136e-16   

              5             6             7             8             9   ...  \
0   4.139322e-06 -5.026621e-07  1.514246e-07 -6.060888e-09 -9.589254e-12  ...   
1  -2.913849e-05  2.880473e-06 -1.250699e-06  2.609822e-09  6.260515e-11  ...   
2  -3.501036e-06 -3.206323e-06 -1.049815e-07  5.742005e-09 -5.071145e-11  ...   
3  -3.724190e-06 -1.716078e-05 -1.198374e-07  5.014978e-09 -3.276804e-10  ...   
4  -6.044048e-06 -6.445529e-07  3.175815e-06 -2.386785e-08 -2.576257e-11  ...   
..           ...           ...           ...           ...           ...  ...   
95 -5.006209e-12 -2.474483e-12 -7.371352e-13 -3.891381e-14 -1.247946e-15  ...   
96 -2.474505e-12  2.992047e-11 -2.395389e-13 -1.284285e-14  5.834935e-16  ...   
97 -7.371205e-13 -2.395402e-13  2.736915e-13 -4.643535e-15  1.237249e-15  ...   
98 -3.891798e-14 -1.284272e-14 -4.641815e-15  1.386602e-15 -1.291668e-15  ...   
99 -1.258799e-15  5.755180e-16  1.234288e-15 -1.288685e-15  5.282962e-19  ...   

              90            91            92            93            94  \
0  -9.547335e-10 -2.387759e-10 -7.999473e-11 -3.281429e-11 -1.561580e-11   
1  -2.391418e-10  2.937689e-10  4.375647e-11  1.502932e-10  2.471119e-11   
2  -8.022226e-11  4.373981e-11  3.736649e-10  6.966232e-12  4.650605e-12   
3  -3.312783e-11  1.502747e-10  6.944275e-12 -7.837534e-10  1.135535e-11   
4  -1.572035e-11  2.465993e-11  4.668992e-12  1.134471e-11 -6.697422e-11   
..           ...           ...           ...           ...           ...   
95 -1.089480e-12 -8.309725e-13 -8.527044e-14 -1.136114e-13 -5.821379e-14   
96 -4.890614e-13 -6.457430e-14 -9.292941e-14 -4.955751e-14 -4.613946e-15   
97 -3.390867e-14 -2.976364e-14 -2.559560e-15 -3.832127e-15  1.222612e-16   
98 -4.504297e-15 -8.017514e-16 -1.067934e-17 -1.223256e-16 -1.029949e-15   
99  5.349638e-18  3.993019e-17 -1.707586e-16 -5.333682e-17 -2.128578e-17   

              95            96            97            98            99  
0  -4.322173e-12 -1.493612e-12 -1.229522e-13 -9.262361e-15 -2.373004e-17  
1   4.163222e-12  7.803618e-12 -1.491222e-12  4.188281e-15  1.413190e-16  
2   2.228691e-11  4.862466e-13  8.100457e-13 -1.541227e-15  7.479754e-17  
3   1.099926e-12 -4.056137e-11  8.437023e-14  1.055888e-14 -7.653431e-16  
4  -2.824555e-11 -5.496907e-12  2.285556e-11 -1.687721e-13 -1.963136e-16  
..           ...           ...           ...           ...           ...  
95  5.361336e-04 -5.407756e-15 -1.982554e-16  3.075975e-17  1.397115e-16  
96 -5.407756e-15  5.361336e-04  1.661752e-17  3.378151e-17 -4.952884e-17  
97 -1.982554e-16  1.661752e-17  5.361336e-04  1.617929e-17  9.747433e-16  
98  3.075975e-17  3.378151e-17  1.617929e-17  5.361336e-04 -1.061214e-16  
99  1.397115e-16 -4.952884e-17  9.747433e-16 -1.061214e-16  5.361336e-04  

[100 rows x 100 columns]

In [71]:
np.linalg.eigvalsh(prior_covariance_matrix)

array([5.06774653e-08, 3.26926654e-07, 9.40885260e-07, 6.32764734e-06,
       1.32512706e-05, 3.83713031e-05, 7.88877401e-05, 9.74387836e-05,
       1.83384559e-04, 2.64569185e-04, 2.82471331e-04, 4.08539537e-04,
       4.08741081e-04, 5.14676602e-04, 5.24210701e-04, 5.24787908e-04,
       5.31813107e-04, 5.32692871e-04, 5.34602170e-04, 5.34934408e-04,
       5.35214969e-04, 5.35832283e-04, 5.35914994e-04, 5.35962268e-04,
       5.35991077e-04, 5.36037118e-04, 5.36039251e-04, 5.36050245e-04,
       5.36084134e-04, 5.36121455e-04, 5.36126931e-04, 5.36130179e-04,
       5.36131442e-04, 5.36132255e-04, 5.36132769e-04, 5.36133432e-04,
       5.36133517e-04, 5.36133522e-04, 5.36133563e-04, 5.36133583e-04,
       5.36133595e-04, 5.36133601e-04, 5.36133605e-04, 5.36133608e-04,
       5.36133609e-04, 5.36133610e-04, 5.36133610e-04, 5.36133611e-04,
       5.36133611e-04, 5.36133611e-04, 5.36133611e-04, 5.36133611e-04,
       5.36133611e-04, 5.36133611e-04, 5.36133611e-04, 5.36133611e-04,
      

In [72]:
# Create a heatmap for the prior covariance matrix
fig1 = px.imshow(
    prior_covariance_matrix,
    labels=dict(x="Index", y="Index", color="Cov."),
    title="Smoothness Prior Covariance Matrix",
    color_continuous_scale="Viridis"
)

# Update layout for better visualization
fig1.update_layout(
    width=800,
    height=800,
    title_x=0.5,
    xaxis_title="Maturity and Strike Indices",
    yaxis_title="Maturity and Strike Indices",
)

# Show the figure
fig1.show()

In [73]:
# Compute the eigenvalues of the prior covariance matrix
eigenvalues = np.linalg.eigvalsh(prior_covariance_matrix)

# Sort eigenvalues by their absolute values in descending order
sorted_eigenvalues = np.sort(eigenvalues)[::-1]

# Calculate the cumulative explained variance
cumulative_explained_variance = np.cumsum(sorted_eigenvalues) / np.sum(sorted_eigenvalues)

# Create a bar plot for the sorted eigenvalues (original values) and a line plot for cumulative explained variance
fig2 = go.Figure()

# Bar plot for eigenvalues
fig2.add_trace(
    go.Bar(
        x=np.arange(1, len(sorted_eigenvalues) + 1),
        y=np.abs(sorted_eigenvalues),
        name="Eigenvalues",
    )
)

# Line plot for cumulative explained variance
fig2.add_trace(
    go.Scatter(
        x=np.arange(1, len(cumulative_explained_variance) + 1),
        y=cumulative_explained_variance,
        name="Cumulative Explained Variance",
        yaxis="y2",
        mode="lines",
    )
)

# Add figure layout
fig2.update_layout(
    title="Eigenvalues and Cumulative Explained Variance",
    xaxis=dict(title="Index of Eigenvalues"),
    yaxis=dict(title="Eigenvalues"),
    yaxis2=dict(
        title="Cumulative Explained Variance",
        overlaying="y",
        side="right",
        showgrid=False,
    ),
    width=900,
    height=900,
    title_x=0.5,
    legend=dict(x=0.1, y=0.9),
)

# Show the figure
fig2.show()

In [74]:
smoothness_prior.sample_smooth_surfaces(9)

array([[ 6.23634465e-03, -2.12055201e-02,  2.10891071e-02,
        -6.93311266e-03, -5.27038917e-03,  4.41439206e-02,
         7.66803643e-03,  2.63006649e-02, -3.89141954e-02,
         1.85011072e-02, -1.01176336e-02,  1.38915270e-02,
        -2.92484396e-02,  5.82910665e-02, -1.67029318e-02,
         7.37459463e-03, -2.82417676e-02, -2.37365784e-02,
        -5.54940159e-02, -4.10139058e-02,  2.54450685e-02,
         4.76130857e-02, -8.40764666e-03, -1.66220629e-02,
         1.59695889e-02, -3.73857464e-03,  9.97957489e-03,
         3.76723127e-03, -2.95215576e-02,  2.36379643e-02,
        -2.40370387e-02, -2.50119410e-03, -1.95980235e-02,
        -2.02032555e-04, -3.81458611e-02, -2.38215010e-03,
        -1.46798047e-02, -1.23727602e-03, -1.07690183e-02,
         7.26202968e-03, -1.54165013e-02,  2.63268649e-02,
        -5.91146247e-02, -2.87974148e-03,  2.64278072e-02,
        -8.59706279e-03, -6.28453155e-03,  4.61189564e-03,
         3.87224074e-03,  1.69339941e-02, -4.81810414e-0

In [75]:
# Sample 9 surface coefficients using the smoothness prior
n_samples = 9
sampled_coefficients = smoothness_prior.sample_smooth_surfaces(n_samples)

# The constant_volatility is set to a reasonable value
constant_volatility = RBFVolatilitySurface.calculate_constant_volatility(
    call_option_dataset["Implied Volatility"],
    call_option_dataset["Time to Maturity"],
    call_option_dataset["Strike Price"],
    risk_free_rate,
    underlying_price
)

# Create the 3x3 subplots
fig = make_subplots(
    rows=3, cols=3,
    subplot_titles=[f"Sample Surface {i+1}" for i in range(n_samples)],
    specs=[[{'type': 'surface'}] * 3] * 3,
    vertical_spacing=0.05, horizontal_spacing=0.05
)

# Loop through the sampled coefficients to generate and plot each surface
for idx, coefficients in enumerate(sampled_coefficients):
    row = (idx // 3) + 1
    col = (idx % 3) + 1
    
    # Initialize the RBFVolatilitySurface class for each set of coefficients
    rbf_surface = RBFVolatilitySurface(
        coefficients=coefficients,
        maturity_times=maturity_times,
        strike_prices=strike_prices,
        maturity_std=maturity_std,
        strike_std=strike_std,
        constant_volatility=constant_volatility
    )

    # Generate the volatility surface over the product grid of times and strikes
    surface_volatilities = np.array([
        rbf_surface.implied_volatility_surface(T, K)
        for T, K in hypothetical_product_grid
    ]).reshape(len(hypothetical_maturity_time_list), len(hypothetical_strike_price_list))

    # Add the surface plot to the subplot
    fig.add_trace(
        go.Surface(
            x=hypothetical_strikes_grid,
            y=hypothetical_maturities_grid,
            z=surface_volatilities,
            showscale=False  # Hide the scale on individual plots
        ),
        row=row, col=col
    )

for i in range(1, 4):  # Rows
    for j in range(1, 4):  # Columns
        fig.update_scenes(
            dict(
                xaxis_title="Strike Price",
                yaxis_title="Time to Maturity",
                zaxis_title="Implied Volatility",
                aspectratio=dict(x=1, y=1, z=0.8)
            ),
            row=i, col=j
        )    

# Update the layout of the figure
fig.update_layout(
    title="Sampled Volatility Surfaces from Smoothness Prior",
    height=1500, width=1500, title_x=0.5,
)

# Show the plot
fig.show()